In [38]:
#Unpickle BC jobs set. 

import pickle
import copy

f = open("/Users/rachelralph/Desktop/bcjobs-data", "rb")
jobs = pickle.load(f)

In [39]:
from nltk import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
import nltk
import ssl


try:
    _create_unverified_https_context = ssl._create_unverified_context
except AttributeError:
    pass
else:
    ssl._create_default_https_context = _create_unverified_https_context

nltk.download('stopwords')
stop_words = set(stopwords.words("english"))

punct = [".", ",", "!", ";", "(", ")", "•", "*", "-", "_"]

stemmer = PorterStemmer()

#Only use first 100 -- mostly likely to be tech related.

for i in range(100):
    
    #Throw away everything but the description. 
    job = jobs[i]["descrip"]
    job = "".join([char for char in job if char not in punct])
    job =  word_tokenize(job)
    job = [stemmer.stem(word) for word in job if word not in stop_words]

    jobs[i] = job
    
    

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/rachelralph/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [40]:
jobs

[['descriptionfortisas',
  'sia',
  'saasbas',
  'servic',
  'combin',
  'network',
  'secur',
  'function',
  'wan',
  'capabl',
  'allow',
  'user',
  'secur',
  'access',
  'internet',
  'anywher',
  'as',
  'team',
  'member',
  'respons',
  'test',
  'endtoend',
  'function',
  'product',
  'you',
  'work',
  'close',
  'multipl',
  'develop',
  'qa',
  'team',
  'verifi',
  'new',
  'featur',
  'regress',
  'test',
  'exist',
  'function',
  'improv',
  'product',
  "'s",
  'usabl',
  'reliabl',
  'perform',
  'job',
  'respons',
  'execut',
  'featur',
  'bug',
  'fix',
  'test',
  'fortisas',
  'sia',
  'applic',
  'use',
  'combin',
  'manual',
  'autom',
  'test',
  'techniqu',
  'autom',
  'frontend',
  'test',
  'use',
  'selenium',
  'java',
  'identifi',
  'document',
  'track',
  'softwar',
  'defect',
  'found',
  'test',
  'work',
  'close',
  'develop',
  'ensur',
  'defect',
  'correctli',
  'identifi',
  'fix',
  'job',
  'skill',
  'requir',
  'experi',
  'softwar'

In [41]:
from gensim import corpora
from gensim.models import LdaModel
from gensim.models import CoherenceModel

jobs = jobs[:100]
dictionary = corpora.Dictionary(jobs)
corpus = [dictionary.doc2bow(job) for job in jobs]

for num_topics in range(3, 21):
    lda_model = LdaModel(corpus, num_topics=num_topics, id2word=dictionary)
    coherence = CoherenceModel(model=lda_model, texts=jobs, dictionary=dictionary, coherence='c_v')
    coherence_score = coherence.get_coherence()
    print(num_topics, ": ", coherence_score)
    

3 :  0.2653899337084945
4 :  0.23900375792338868
5 :  0.25923244226749553
6 :  0.2606344167030179
7 :  0.24633814523037462
8 :  0.24373550547587977
9 :  0.27172053488659376
10 :  0.2966095045425073
11 :  0.2677130971396555
12 :  0.28086739750265927
13 :  0.256745197129325
14 :  0.2594299096033056
15 :  0.2490973293429596
16 :  0.2506616065400989
17 :  0.2520477388584162
18 :  0.2733624170087998
19 :  0.2594931756583204
20 :  0.28803585176963714


In [42]:
!pip install pyLDAvis


[notice] A new release of pip is available: 23.1.2 -> 24.0
[notice] To update, run: pip install --upgrade pip


In [43]:
#15 topics is currently the best. 

lda_model = LdaModel(corpus, num_topics=15, id2word=dictionary)

import pyLDAvis.gensim_models as gensimvis
import pyLDAvis

vis_data = gensimvis.prepare(lda_model, corpus, dictionary)
pyLDAvis.display(vis_data)

So LDA is always a shot in the dark for a few reasons: 

<ol>
  <li>It is an unsupervised learning algorithm -- we have no control over how it clusters things, it just does.</li>
  <li>A few companies are overrepresented in our dataset, such as Deloitte. Companies will usually structure there job posting in a
      similar way, so it is easy to sort based on company instead of based on role. (Note how many categories Deloit is a top word!)</li>
  <li>We would like it to base it off of the kind of software developer role. And some of the keywords do relate to that ("test") is one of the top words for a category. But most of the top words are things like required, skill and included, which are not helpful to determining this stuff.</li>
</ol>

I do want to try this categorization method on sentences though -- just to see if it comes up with anything interesting. For example, if "degree" is a top word in one of the categories, it might be useful. That said, I still expect it will be highly biased towards the company that posted the role. 

In [1]:
#Unpickle BC jobs set. 

import pickle
import copy

f = open("/Users/rachelralph/Desktop/bcjobs-data", "rb")
jobs = pickle.load(f)

In [2]:
from nltk import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
import nltk
import ssl

job_sentences =[]

for job in jobs[:50]:

    job = job["descrip"]
    job = job.split("•")
    for i in job:
        i = i.split("\n")
        for j in i:
            j = j.split(".")
            for k in j:
                job_sentences.append(k)
    

In [3]:
#Remove whitespace
i = 0
while i < len(job_sentences):
    job_sentences[i] = job_sentences[i].strip()
    if job_sentences[i] == "":
        job_sentences.pop(i)
    else:
        i+= 1
job_sentences

['DescriptionFortiSASE SIA is a SaaS-based service that combines network and security functions with WAN capabilities, which allows users to securely access the Internet from anywhere',
 'As a team member, you will be responsible for testing the end-to-end functionality of the product',
 "You will be working closely with multiple development and QA teams to verify new features, regression test existing functionalities and improve the product's usability, reliability, and performance",
 'Job Responsibilities Execute feature and bug fix testing for the FortiSASE SIA application using a combination of manual and automated testing techniques',
 'Automate front-end testing using Selenium (Java)',
 'Identify, document, and track software defects found during testing',
 'Work closely with developers to ensure defects are correctly identified and fixed',
 'Job Skills Required Experience in software testing, including web application and REST API testing',
 'Knowledge of TCP/IP networking, fire

In [4]:
from nltk import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
import nltk
import ssl


try:
    _create_unverified_https_context = ssl._create_unverified_context
except AttributeError:
    pass
else:
    ssl._create_default_https_context = _create_unverified_https_context

nltk.download('stopwords')
stop_words = set(stopwords.words("english"))

punct = [".", ",", "!", ";", "(", ")", "•", "*", "-", "_", "#", ":", ",", "#", "\""]

stemmer = PorterStemmer()

#Only use first 100 -- mostly likely to be tech related.

for i in range(len(job_sentences)):
    
    job_sentences[i] = "".join([char for char in job_sentences[i] if char not in punct and not char.isnumeric()])
    job_sentences[i] =  word_tokenize(job_sentences[i])
    job_sentences[i] = [stemmer.stem(word) for word in job_sentences[i] if word not in stop_words]

job_sentences

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/rachelralph/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


[['descriptionfortisas',
  'sia',
  'saasbas',
  'servic',
  'combin',
  'network',
  'secur',
  'function',
  'wan',
  'capabl',
  'allow',
  'user',
  'secur',
  'access',
  'internet',
  'anywher'],
 ['as',
  'team',
  'member',
  'respons',
  'test',
  'endtoend',
  'function',
  'product'],
 ['you',
  'work',
  'close',
  'multipl',
  'develop',
  'qa',
  'team',
  'verifi',
  'new',
  'featur',
  'regress',
  'test',
  'exist',
  'function',
  'improv',
  'product',
  "'s",
  'usabl',
  'reliabl',
  'perform'],
 ['job',
  'respons',
  'execut',
  'featur',
  'bug',
  'fix',
  'test',
  'fortisas',
  'sia',
  'applic',
  'use',
  'combin',
  'manual',
  'autom',
  'test',
  'techniqu'],
 ['autom', 'frontend', 'test', 'use', 'selenium', 'java'],
 ['identifi', 'document', 'track', 'softwar', 'defect', 'found', 'test'],
 ['work',
  'close',
  'develop',
  'ensur',
  'defect',
  'correctli',
  'identifi',
  'fix'],
 ['job',
  'skill',
  'requir',
  'experi',
  'softwar',
  'test',
  '

In [5]:
from gensim import corpora
from gensim.models import LdaModel
from gensim.models import CoherenceModel

dictionary = corpora.Dictionary(job_sentences)
corpus = [dictionary.doc2bow(job_sentence) for job_sentence in job_sentences]

for num_topics in range(3, 10):
    lda_model = LdaModel(corpus, num_topics=num_topics, id2word=dictionary)
    coherence = CoherenceModel(model=lda_model, texts=job_sentences, dictionary=dictionary, coherence='c_v')
    coherence_score = coherence.get_coherence()
    print(num_topics, ": ", coherence_score)

3 :  0.4043008611096624
4 :  0.3686006088009402
5 :  0.41011277429966764
6 :  0.3809856046621169
7 :  0.36341775280266514
8 :  0.3423903695329412
9 :  0.35895900302898326


In [6]:
for passes in range(1, 20):
    lda_model = LdaModel(corpus, num_topics=5, id2word=dictionary, passes = passes)
    coherence = CoherenceModel(model=lda_model, texts=job_sentences, dictionary=dictionary, coherence='c_v')
    coherence_score = coherence.get_coherence()
    print(passes, ": ", coherence_score)

1 :  0.36556067952867843
2 :  0.42173136197412936
3 :  0.33127920497934565
4 :  0.36612198616901376
5 :  0.401957997831237
6 :  0.3820690771976091
7 :  0.39660894936599705
8 :  0.3780419417711761
9 :  0.3080977712700819
10 :  0.37607317518022737
11 :  0.39436283515116066
12 :  0.3520645446193774
13 :  0.4263631318130237
14 :  0.3739790695062342
15 :  0.3723942205074872
16 :  0.3468731680086838
17 :  0.39110417323598623
18 :  0.35953887573575505
19 :  0.38229656822938973


In [8]:
lda_model = LdaModel(corpus, num_topics=5, id2word=dictionary, passes = 13)

import pyLDAvis.gensim_models as gensimvis
import pyLDAvis

vis_data = gensimvis.prepare(lda_model, corpus, dictionary)
pyLDAvis.display(vis_data)

In [13]:
lda_model.print_topics()

[(0,
  '0.026*"deloitt" + 0.014*"client" + 0.013*"secur" + 0.012*"categori" + 0.011*"peopl" + 0.010*"experi" + 0.010*"servic" + 0.009*"our" + 0.009*"make" + 0.009*"purpos"'),
 (1,
  '0.016*"we" + 0.015*"develop" + 0.014*"skill" + 0.013*"abil" + 0.013*"team" + 0.012*"commun" + 0.010*"softwar" + 0.009*"work" + 0.008*"support" + 0.008*"peopl"'),
 (2,
  '0.021*"develop" + 0.013*"manag" + 0.011*"design" + 0.011*"product" + 0.010*"technolog" + 0.010*"team" + 0.010*"want" + 0.009*"like" + 0.009*"we" + 0.009*"work"'),
 (3,
  '0.021*"experi" + 0.017*"includ" + 0.016*"deloitt" + 0.013*"work" + 0.012*"$" + 0.011*"peopl" + 0.011*"develop" + 0.010*"commun" + 0.010*"offer" + 0.010*"``"'),
 (4,
  '0.033*"experi" + 0.020*"technolog" + 0.019*"secur" + 0.015*"program" + 0.014*"inform" + 0.014*"softwar" + 0.014*"develop" + 0.012*"be" + 0.012*"comput" + 0.011*"degre"')]

In [14]:
f = open("labeled_sentneces.txt", "r")

text = str(f.read())
print(type(text))
f.close()

sentences = text.split("\n")

labeled_sentences = []

for sentence in sentences:
    labeled_sentence = sentence.split(":")
    if(len(labeled_sentence) == 2):
        labeled_sentences.append(labeled_sentence)

len(labeled_sentences)

<class 'str'>


191

In [17]:
labeled_sentences[0]

['WSP is committed to the principles of employment equity. ', ' CJ']

In [21]:
dictionary = corpora.Dictionary([labeled_sentence[0] for labeled_sentence in labeled_sentences])
corpus = [dictionary.doc2bow(labeled_sentence[0]) for labeled_sentence in labeled_sentences]

TypeError: doc2bow expects an array of unicode tokens on input, not a single string